# Mail Preprocessor

In [40]:
import os
import email
import pandas as pd
import re
import emoji
import mailparser
from bs4 import BeautifulSoup
import quopri
import mailparser
from bs4 import Comment
import time


def decode_payload(payload):
    if payload is None:
        return None, 0

    encodings = ['utf-8', 'cp437', 'ISO-8859-1']
    for encoding in encodings:
        try:
            decoded_text = quopri.decodestring(payload).decode(encoding, errors='replace')
            return decoded_text, decoded_text.count('�')
        except UnicodeDecodeError:
            pass
    return None, 0

def extract_info_from_email(file_path):

    # mail = mailparser.parse_from_file(file_path)
    encodings = [
                'utf-8',          # Most common encoding for web content
                'cp437',          # Original character set of IBM PC (DOS)
                'ISO-8859-1',     # Western European/Latin-1
                'ISO-8859-2',     # Central and Eastern European/Latin-2
                'ISO-8859-3',     # South European/Latin-3
                'ISO-8859-4',     # North European/Latin-4
                'ISO-8859-5',     # Latin/Cyrillic
                'ISO-8859-6',     # Latin/Arabic
                'windows-1256',   # Arabic
                'koi8-r',         # Russian
                'koi8-u',         # Ukrainian
                'big5',           # Traditional Chinese
                'gb2312',         # Simplified Chinese
                'euc-kr',         # Korean
                'shift_jis',      # Japanese
            ]
    mail = None

    for encoding in encodings:
        try:
            with open(file_path, 'r', encoding=encoding, errors='replace') as file:
                file_content = file.read()
            mail = mailparser.parse_from_string(file_content)
            break  # Break the loop if parsing is successful
        except (UnicodeDecodeError, Exception) as e:
            print(f"Failed to parse {file_path} with encoding {encoding} due to: {e}")
            # Optionally, you can log the error or handle it as required

    if not mail:
        print(f"Failed to parse {file_path} with all tried encodings")
        return None
    
    with open(file_path, 'r', encoding='cp437', errors='replace') as f:
        msg = email.message_from_file(f)

        unknown_chars_count = 0
        body = ''
        unsubscribe_links = []
        comments = []
        soup = None  # Initialize soup here

        if msg.is_multipart():
            for part in msg.walk():
                content_disposition = str(part.get("Content-Disposition"))
                if "attachment" not in content_disposition:
                    part_body, unknown_count = decode_payload(part.get_payload(decode=True))
                    if part_body:
                        body += part_body
                        unknown_chars_count += unknown_count

                        if part_body.strip():  # Check if part_body is not empty
                            try:
                                part_soup = BeautifulSoup(part_body, 'html5lib')
                                unsubscribe_links.extend([link['href'] for link in part_soup.find_all('a', href=True) if "unsubscribe" in link.text.lower()])
                                if soup is None:
                                    soup = part_soup
                                    # Extract comments from the soup
                                    comments = [str(comment) for comment in soup.find_all(string=lambda text: isinstance(text, Comment))]
                            except Exception as e:
                                print(f"Failed to parse part of {file_path} with html5lib due to: {e}")

        else:
            body, unknown_count = decode_payload(msg.get_payload(decode=True))
            unknown_chars_count += unknown_count

            try:
                soup = BeautifulSoup(body, 'html5lib')

                # Define a list of possible unsubscribe indicators
                unsubscribe_indicators = ["unsubscribe", "opt out", "opt-out", "stop receiving", "email preferences", "subscription settings"]

                # Search for links that contain any of the indicators in their text or title attribute
                unsubscribe_links = [link['href'] for link in soup.find_all('a', href=True) if any(indicator in link.get_text().lower() or indicator in link.get('title', '').lower() for indicator in unsubscribe_indicators)]

                # Additionally, check in the href attribute for some common patterns
                unsubscribe_links.extend([link['href'] for link in soup.find_all('a', href=True) if "unsubscribe" in link['href'].lower() or "optout" in link['href'].lower()])

                comments = [str(comment) for comment in soup.find_all(string=lambda text: isinstance(text, Comment))]
            except Exception as e:
                print(f"Failed to parse {file_path} with html5lib due to: {e}")

        if not body:
            print(f"No body content found for {file_path}")
            return None

        # Count all occurrences of "http:" and "https:" in the email's body and subject
        link_pattern = re.compile(r'https?:')
        total_links_in_body = len(link_pattern.findall(body))
        total_links_in_subject = len(link_pattern.findall(mail.subject))
        total_links_in_comments = len(link_pattern.findall(' '.join(comments)))

        total_links = total_links_in_body + total_links_in_subject + total_links_in_comments

        if soup:
            tracking_pixel = len(soup.find_all('img', width='1', height='1')) > 0
            # total_links = len(soup.find_all('a'))

        else:
            tracking_pixel = False
            total_links = 0

        dkim_signature = 'Present' if msg.get('DKIM-Signature') else 'Absent'


    return {
        'filename': os.path.basename(file_path),
        'body': mail.body,
        'subject': mail.subject,
        'comments': ' '.join(comments),
        'text_plain': 1 if mail.text_plain else 0,
        'text_html': 1 if mail.text_html else 0,
        'text_not_managed': 1 if mail.text_not_managed else 0,
        'defects': str(mail.defects),
        'defects_categories': str(mail.defects_categories),
        'number of unsubscribe links': len(unsubscribe_links),
        'number of undecodable characters': unknown_chars_count,
        'tracking pixel present': tracking_pixel,
        'total num of images': len(soup.find_all('img')) if soup else 0,
        'total links in email': total_links,
        'email size (bytes)': len(body),
        'dkim-signature': dkim_signature
    }




warranted = False
unwarranted = True

infos = []
failed_files = []



start_time = time.time()

# Use for warranted
if warranted:

    # Directory to search
    directory = 'C:\\Users\\ericb\\Desktop\\Research\\Primary@gmail.com\\Cleaned_Mail\\2023\\'
    output_directory = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\'

    # Ensure output directory exists
    if not os.path.exists(output_directory):
        os.makedirs(output_directory)

    for dirpath, dirnames, filenames in os.walk(directory):
        print(f"Processing {dirpath}")
        for file_name in filenames:
            file_path = os.path.join(dirpath, file_name)
            info = extract_info_from_email(file_path)
            if info:
                infos.append(info)

if unwarranted:

    directory = 'C:\\Users\\ericb\\Desktop\\Research\\Bruce\\'
    output_directory = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\'

    # Ensure output directory exists
    if not os.path.exists(output_directory):
        os.makedirs(output_directory)

    for dirpath, dirnames, filenames in os.walk(directory):
        # Split the directory path to get individual parts
        path_parts = dirpath.split(os.sep)

        # Check if the path has at least two parts (to avoid index error)
        # and if the second last part is a year between 2018 and 2023
        if len(path_parts) > 2 and path_parts[-2].isdigit() and 2018 <= int(path_parts[-2]) <= 2023:
            print(f"Processing {dirpath}")
            for file_name in filenames:
                file_path = os.path.join(dirpath, file_name)
                info = extract_info_from_email(file_path)
                if info:
                    infos.append(info)
        else:
            print(f"Skipping {dirpath}")

if infos:
    df = pd.DataFrame(infos)
    if not df.empty:
        if warranted:
            csv_path = os.path.join(output_directory, f"warranted_preprocessed_files_v2.csv")
        elif unwarranted:
            csv_path = os.path.join(output_directory, f"unwarranted_preprocessed_files_v2.csv")
        print('saving to excel')
        df.to_csv(csv_path, index=False)

# Saving the failed filenames to a CSV
if failed_files:
    failed_df = pd.DataFrame({'Failed Files': failed_files})
    failed_df.to_csv("failed_files.csv", index=False)
    print(f"Failed to parse {len(failed_files)} files. See failed_files.csv for details.")

print("Script execution completed.")
print(f"Time taken: {time.time() - start_time} seconds")

Skipping C:\Users\ericb\Desktop\Research\Bruce\
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\01
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\02
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\03
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\04
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\05
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\06
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\07
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\08
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\09
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\10
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\11
Skipping C:\Users\ericb\Desktop\Research\Bruce\2013\12
Skipping C:\Users\ericb\Desktop\Research\Bruce\2014
Skipping C:\Users\ericb\Desktop\Research\Bruce\2014\2014
Skipping C:\Users\ericb\Desktop\Research\Bruce\2014\2014\01
Skipping C:\Users\ericb\Desktop\Research\Bruce\2014\2014\02
Skipping C:

c:\Users\ericb\anaconda3\envs\machinelearning_20220719\lib\site-packages\bs4\__init__.py:439: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  MarkupResemblesLocatorWarning
More than one match found for (?:(?:^|\s)from\s+(?P<from>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+by|\s+with(?! cipher)|\s+id|\s+for|\s+via|;)) in from 61.206.120.243 153.127.216.225 by 103.30.243.137 Postfix with ESMTP 20151028 S8257F224EB04475AA2B8A21F37B22469 id 196042D6 for <bruce@bruce-guenter.dyndns.org> from <mailmaster@fut-----ure2o50.com>; Mon, 1 Jan 2018 21:31:52 +0900 JST
More than one match found for (?:(?:^|\s)from\s+(?P<from>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+by|\s+with(?! cipher)|\s+id|\s+for|\s+via|;)) in from 61.206.120.243 153.127.216.225 by 103.30.243.137 Postfix with ESMTP 20151028 S8257F224EB04475AA2B8A21F37B22469 id 196042D6 for <bruce@bruce-guenter.dyndn

Processing C:\Users\ericb\Desktop\Research\Bruce\2018\02


More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in by mail.three.co.id Postfix, from userid 359 id DEAD6B16CBA; Fri, 02 Feb 2018 11:14:06 +0700
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in by mail.three.co.id Postfix, from userid 359 id DEAD6B16CBA; Fri, 02 Feb 2018 11:14:06 +0700
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in by mail.unifa.ac.id Postfix, from userid 952 id 8047EA4DD14; Fri, 02 Feb 2018 10:58:00 +0530
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in by mail.unifa.ac.id Postfix, from userid 952 id 8047EA4DD14; Fri, 02 Feb 2018 10:58:00 +0530
More tha

Processing C:\Users\ericb\Desktop\Research\Bruce\2018\03


...

Processing C:\Users\ericb\Desktop\Research\Bruce\2022\11
Processing C:\Users\ericb\Desktop\Research\Bruce\2022\12
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2022\12\1670307128.1385316_261.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2022\12\1670989087.487487_81.txt
Skipping C:\Users\ericb\Desktop\Research\Bruce\2023
Processing C:\Users\ericb\Desktop\Research\Bruce\2023\01
Processing C:\Users\ericb\Desktop\Research\Bruce\2023\02
Processing C:\Users\ericb\Desktop\Research\Bruce\2023\03


Email content 'rfc822-headers' not handled


Processing C:\Users\ericb\Desktop\Research\Bruce\2023\04


More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in from localhost localhost 127.0.0.1 by mail.bekasikab.go.id Postfix with ESMTP id A1BDC24779EC8; Sat, 22 Apr 2023 11:47:38 +0700 WIB
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in from mail.bekasikab.go.id 127.0.0.1 by localhost mail.bekasikab.go.id 127.0.0.1 amavisd-new, port 10032 with ESMTP id hdofGn3MIDcD; Sat, 22 Apr 2023 11:47:38 +0700 WIB
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s+from|\s+by|\s+with(?! cipher)|\s+for|\s+via|;)) in from localhost localhost 127.0.0.1 by mail.bekasikab.go.id Postfix with ESMTP id 868F93681B948; Sat, 22 Apr 2023 03:00:43 +0700 WIB
More than one match found for [^\w](?:id\s+(?P<id>.+?)(?:\s*[(]?envelope-from|\s*[(]?envelope-sender|\s

Processing C:\Users\ericb\Desktop\Research\Bruce\2023\05
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1684124888.868340_1.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1684771329.1077101_3.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1684771341.1077103_61.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1685167221.1203693_1.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1685335739.1244660_1.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\05\1685335745.1244664_19.txt
Processing C:\Users\ericb\Desktop\Research\Bruce\2023\06
Processing C:\Users\ericb\Desktop\Research\Bruce\2023\07
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\07\1689703443.378259_1.txt
No body content found for C:\Users\ericb\Desktop\Research\Bruce\2023\07\1690784733.1132874_5.txt
Processing C:\Users\ericb\Desktop\Research\Bruce\2023

In [41]:
# Now that I have the data, I can clean the textual data for use in the model
# print(df['body'][0])
df.head(50)

filename  \
0   1514898318.13268_223.txt   
1   1514898318.13268_225.txt   
2   1514898318.13268_227.txt   
3   1514898318.13268_229.txt   
4      1514911925.5197_1.txt   
5      1514911941.5199_1.txt   
6    1514911941.5199_101.txt   
7    1514911941.5199_103.txt   
8    1514911941.5199_105.txt   
9    1514911941.5199_107.txt   
10   1514911941.5199_109.txt   
11    1514911941.5199_11.txt   
12   1514911941.5199_111.txt   
13   1514911941.5199_113.txt   
14   1514911941.5199_115.txt   
15   1514911941.5199_117.txt   
16   1514911941.5199_119.txt   
17   1514911941.5199_121.txt   
18   1514911941.5199_123.txt   
19   1514911941.5199_125.txt   
20   1514911941.5199_127.txt   
21   1514911941.5199_129.txt   
22    1514911941.5199_13.txt   
23   1514911941.5199_131.txt   
24   1514911941.5199_133.txt   
25   1514911941.5199_135.txt   
26   1514911941.5199_137.txt   
27   1514911941.5199_139.txt   
28   1514911941.5199_141.txt   
29   1514911941.5199_143.txt   
30   1514911941.5199_145.txt   
31   1514911941.5199_147.txt   
32   1514911941.5199_149.txt   
33    1514911941.5199_15.txt   
34   1514911941.5199_151.txt   
35   1514911941.5199_153.txt   
36   1514911941.5199_155.txt   
37   1514911941.5199_157.txt   
38   1514911941.5199_159.txt   
39   1514911941.5199_161.txt   
40   1514911941.5199_163.txt   
41   1514911941.5199_165.txt   
42   1514911941.5199_167.txt   
43   1514911941.5199_169.txt   
44    1514911941.5199_17.txt   
45   1514911941.5199_171.txt   
46   1514911941.5199_173.txt   
47   1514911941.5199_175.txt   
48   1514911941.5199_177.txt   
49   1514911941.5199_179.txt   

                                                 body  \
0   <html><body><span style="font-family:Verdana; ...   
1   Science of Numerological Analysis\n\n\nhttp://...   
2   Science of Numerological Analysis\n\n\nhttp://...   
3   \n\nThese chicks are looking for casual sex an...   
4   附件为18年计划表 \n--- mail_boundary ---\nContent-Typ...   
5   Voted Top Gift for 2017!  Stealth SmartCam!  F...   
6   <a href="http://vf6nasru.com/log_index.php?pag...   
7   <a href="http://p8mxvmft.com/log_index.php?pag...   
8   <a href="http://p8mxvmft.com/log_index.php?pag...   
9   <a href="http://sm2ecizx.com/log_index.php?pag...   
10  <a href="http://vf6nasru.com/log_index.php?pag...   
11  Application facts - no out of pocket costs\n\n...   
12  <a href="http://sm2ecizx.com/log_index.php?pag...   
13  <a href="http://sm2ecizx.com/log_index.php?pag...   
14  <a href="http://sm2ecizx.com/log_index.php?pag...   
15  <a href="http://p8mxvmft.com/log_index.php?pag...   
16  <a href="http://vf6nasru.com/log_index.php?pag...   
17             bruce:您好！ \r\n                     ...   
18  <a href="http://sm2ecizx.com/log_index.php?pag...   
19  <a href="http://sm2ecizx.com/log_index.php?pag...   
20  <a href="http://vf6nasru.com/log_index.php?pag...   
21  <a href="http://q7lkfapc.com/log_index.php?pag...   
22  Relieve Anxiety Today! Try CBD!\n\nhttp://www....   
23  <a href="http://sm2ecizx.com/log_index.php?pag...   
24  <a href="http://vf6nasru.com/log_index.php?pag...   
25  bruce@bruce-guenter.dyndns.org<br>\r\nPC MALLを...   
26  \nhttp://rhkzd.zbonmobuugorto.com/as/member/me...   
27  The only thing you will need is:EMAIL\nThis pr...   
28  <a href="http://sm2ecizx.com/log_index.php?pag...   
29  <a href="http://vf6nasru.com/log_index.php?pag...   
30  <a href="http://q7lkfapc.com/log_index.php?pag...   
31  <a href="http://q7lkfapc.com/log_index.php?pag...   
32  ���\\ufffdO�ɘA��������������񂾂��ǑS�R�A�����ĂȂ��...   
33  Are your meds part of America's deadly new hea...   
34  <a href="http://p8mxvmft.com/log_index.php?pag...   
35  <a href="http://p8mxvmft.com/log_index.php?pag...   
36  <a href="http://p8mxvmft.com/log_index.php?pag...   
37  bruce@bruce-guenter.dyndns.org<br>\r\n<br>\r\n...   
38  <a href="http://sm2ecizx.com/log_index.php?pag...   
39  \nhttp://riryp.zbonmobuugorto.com/as/member/me...   
40  \nhttp://aiknp.zbonmobuugorto.com/as/member/me

In [42]:
# output_csv = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_preprocessed_files.csv'
output_csv = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_preprocessed_files_v2.csv'
# Open the CSV file and read it into a DataFrame
df_to_clean = pd.read_csv(output_csv)

In [43]:
import re
import emoji
from bs4 import BeautifulSoup, NavigableString, Tag
import quopri
import base64

def replace_emojis(text):
    # Replace emojis with their text description
    return emoji.demojize(text, delimiters=("", ""))

# def replace_urls_based_on_context(html_content):
#     soup = BeautifulSoup(html_content, 'lxml')
#     for a_tag in soup.find_all('a'):
#         href = a_tag.get('href', '')
#         url_type = 'UNSAFE_' if href.startswith('http://') else ''
#         if a_tag.img:
#             a_tag.string = f'{url_type}IMAGE_URL'
#         elif isinstance(a_tag.next, NavigableString) and a_tag.next.strip():
#             a_tag.string = f'{url_type}LINK_URL'
#         else:
#             a_tag.string = f'{url_type}BUTTON_URL'
#     return str(soup)

def replace_elements_in_html(soup):

    # Replace URLs in 'a' tags
    for a_tag in soup.find_all('a'):
        href = a_tag.get('href', '')
        url_type = ' UNSAFE_' if href.startswith('http://') else ' '
        if a_tag.img:
            a_tag.string = f'{url_type}IMAGE_URL '
        elif isinstance(a_tag.next, NavigableString) and a_tag.next.strip():
            a_tag.string = f'{url_type}LINK_URL '
        else:
            a_tag.string = f'{url_type}BUTTON_URL '

    # Replace src in 'img' tags not wrapped in 'a' tags
    for img_tag in soup.find_all('img'):
        if img_tag.parent.name != 'a':  # Checks if the img tag is not a child of an 'a' tag
            src = img_tag.get('src', '')
            url_type = ' UNSAFE_' if src.startswith('http://') else ''
            new_tag = soup.new_tag("span")
            new_tag.string = f'{url_type}IMAGE_URL '
            img_tag.replace_with(new_tag)

    # Replace buttons - you need to define what you consider as a button
    for button_tag in soup.find_all(['button', 'input']):
        if button_tag.get('type') in ['button', 'submit']:
            button_tag.string = ' BUTTON_URL '

    # Optionally, handle styled divs or other elements used as buttons
    for div_tag in soup.find_all('div', class_='button-style'):  # Example class name
        div_tag.string = ' BUTTON_URL '

    return soup

def replace_urls_in_text(text):
    http_url_pattern = re.compile(r'http://\S+')
    text = http_url_pattern.sub(' UNSAFE_LINK_URL ', text)
    https_url_pattern = re.compile(r'https://\S+')
    text = https_url_pattern.sub(' LINK_URL ', text)
    return text

def decode_quoted_printable(input_data):
    if isinstance(input_data, bytes):
        return quopri.decodestring(input_data).decode('utf-8', errors='replace')
    else:
        return quopri.decodestring(input_data.encode()).decode('utf-8', errors='replace')

def decode_base64(text):
    return base64.b64decode(text).decode('utf-8', errors='replace')

def clean_text(raw_text):
    # If raw_text is None, return an empty string or you could return None depending on your requirement
    if raw_text is None:
        return ''
        
    if not isinstance(raw_text, str):
        # If raw_text is not a string, return it as is or convert it to a string
        return raw_text

    #Remove line breaks and continuation equals signs
    raw_text = re.sub(r'=\n', '', raw_text)
    # Decode any quoted-printable text
    raw_text = quopri.decodestring(raw_text.encode()).decode('utf-8', errors='replace')

    # Create a BeautifulSoup object
    soup = BeautifulSoup(raw_text, 'lxml')

    # Apply replacements for elements in HTML content
    soup = replace_elements_in_html(soup)

    # Remove style and script tags and their content
    for tag in soup(['style', 'script', 'img']):
        tag.decompose()

    # # Replace URLs in 'a' tags
    # for a_tag in soup.find_all('a'):
    #     href = a_tag.get('href', '')
    #     url_type = 'UNSAFE ' if href.startswith('http://') else ''
    #     if a_tag.img:
    #         a_tag.string = f'{url_type}IMAGE URL'
    #     elif isinstance(a_tag.next, NavigableString) and a_tag.next.strip():
    #         a_tag.string = f'{url_type}LINK URL'
    #     else:
    #         a_tag.string = f'{url_type}BUTTON URL'

    # Now proceed with extracting text and further cleaning
    text = soup.get_text(separator=' ', strip=True)
    text = replace_emojis(text)

    text = replace_urls_in_text(text)

    # Remove any remaining HTML encoded characters
    text = re.sub(r'&[a-zA-Z0-9#]+;', '', text)
    
    # Remove extra whitespace
    text = re.sub(r'\s+', ' ', text)
    
    # Remove Zero Width Non-Joiner characters
    text = text.replace('\u200b', '')  # Unicode for ZWNBSP
    text = text.replace('\u200c', '')  # Unicode for ZWNJ
    text = text.replace('\u200d', '')  # Unicode for ZWJ
    text = text.replace('\u200e', '')  # Unicode for LEFT-TO-RIGHT MARK
    text = text.replace('\u200f', '')  # Unicode for RIGHT-TO-LEFT MARK


    # Strip string of leading/trailing whitespace
    return text.strip()


In [45]:


# run the clean_text function on the subject and body columns
df_to_clean['subject'] = df_to_clean['subject'].apply(lambda x: clean_text(x) if x is not None else 'No Subject Found in email.')
df_to_clean['body'] = df_to_clean['body'].apply(lambda x: clean_text(x) if x is not None else 'No Body Found in email.')
df_to_clean['comments'] = df_to_clean['comments'].apply(lambda x: clean_text(x) if x is not None else'No Comments Found in email.')
print(df_to_clean['body'][0])


c:\Users\ericb\anaconda3\envs\machinelearning_20220719\lib\site-packages\bs4\__init__.py:439: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  MarkupResemblesLocatorWarning
c:\Users\ericb\anaconda3\envs\machinelearning_20220719\lib\site-packages\bs4\__init__.py:408: MarkupResemblesLocatorWarning: The input looks more like a URL than markup. You may want to use an HTTP client like requests to get the document behind the URL, and feed that document to Beautiful Soup.
  MarkupResemblesLocatorWarning


Can we talk ?


In [46]:
# Save the cleaned data to a new CSV
# df_to_clean.to_csv('C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_v2.csv', index=False)
df_to_clean.to_csv('C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_v2.csv', index=False)

In [47]:

df_to_clean.head(10)

filename  \
0  1514898318.13268_223.txt   
1  1514898318.13268_225.txt   
2  1514898318.13268_227.txt   
3  1514898318.13268_229.txt   
4     1514911925.5197_1.txt   
5     1514911941.5199_1.txt   
6   1514911941.5199_101.txt   
7   1514911941.5199_103.txt   
8   1514911941.5199_105.txt   
9   1514911941.5199_107.txt   

                                                body  \
0                                      Can we talk ?   
1  Science of Numerological Analysis UNSAFE_LINK_...   
2  Science of Numerological Analysis UNSAFE_LINK_...   
3  These chicks are looking for casual sex and di...   
4  附件为18年计划表 --- mail_boundary --- Content-Type: ...   
5  Voted Top Gift for 2017! Stealth SmartCam! FRE...   
6                    UNSAFE_LINK_URL 】｀●┠◎´□⌒´∴㎡┳′〔★   
7  UNSAFE_LINK_URL male_sign〔√┘´＾⊂┓｝male_sign∫⊆┸┠...   
8                UNSAFE_LINK_URL ゝ｛〃→⌒[Å∪≒〒×┣∇Å℃┛＼〓∈   
9                          UNSAFE_LINK_URL 「≦∬∥％┴▲☆′   

                                             subject comments  text_plain  \
0                                                 HI      NaN           0   
1                  Science of Numerological Analysis      NaN           1   
2                  Science of Numerological Analysis      NaN           1   
3         These chicks are looking for a booty call.      NaN           1   
4                                        回复：2018年计划表      NaN           1   
5  Voted Top Gift for 2017! Stealth SmartCam! FRE...      NaN           1   
6                                   お早う御座います。届いてますか？      NaN           0   
7  このメールが最後のご連絡になる可能性も少なくはありません。誤解を招かない為にも、ちゃんと事情...      NaN           0   
8  貴方の口座を教えて下さいますか？その口座に「1億円」の支援金、私から貴方への「返済不要の支援...      NaN           0   
9                              ※ご入金がありましたので至急ご確認下さい※      NaN           0   

   text_html  text_not_managed defects defects_categories  \
0          1                 0      []              set()   
1          1                 0      []              set()   
2          1                 0      []              set()   
3          1                 0      []              set()   
4          1                 0      []              set()   
5          1                 0      []              set()   
6          1                 0      []              set()   
7          1                 0      []              set()   
8          1                 0      []              set()   
9          1                 0      []              set()   

   number of unsubscribe links  number of undecodable characters  \
0                            0                                 0   
1                            1                                 2   
2                            1                                 2   
3                            0                                 0   
4                            0                                 0   
5                            0                                 0   
6                            0                                 0   
7                            0                                 0   
8                            0                                 0   
9                            0                                 0   

   tracking pixel present  total num of images  total links in email  \
0                   False                    0                     0   
1                   False                    0                    23   
2                   False                    0                    23   
3                   False                    0                    11   
4                   False                    0                     0   
5                   False                    0                    13   
6                   False                    0                     2   
7                   False                    0                     2   
8                   False                    0                     2   
9                   False                    0                     2   

# Drop the duplicate emails from the list of emails

In [65]:
# Path to your CSV file
input_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_v2.csv'
output_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_no_duplicates_v2.csv'
# input_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_v2.csv'
# output_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_no_duplicates_v2.csv'


# Load the CSV file into a DataFrame
df = pd.read_csv(input_csv_path)

# Store the original number of rows
original_row_count = df.shape[0]

# Remove duplicate rows based on both 'subject' and 'body' columns
df_cleaned = df.drop_duplicates(subset=['subject', 'body'], keep='first')

# Calculate the number of removed rows
removed_rows_count = original_row_count - df_cleaned.shape[0]

# Save the cleaned DataFrame back to a new CSV file
df_cleaned.to_csv(output_csv_path, index=False)

print(f"Cleaned CSV saved to {output_csv_path}")
print(f"Number of duplicate rows removed based on 'subject' and 'body': {removed_rows_count}")

Cleaned CSV saved to C:\Users\ericb\Desktop\Research\542_Project\cleaned_data\unwarranted_data\unwarranted_cleaned_data_no_duplicates_v2.csv
Number of duplicate rows removed based on 'subject' and 'body': 53336


In [ ]:
print(df_to_clean['body'][1])

# save df_to_clean['body'][i] to txt file
for i in range (0, len(df_to_clean['body'])):
    with open('C:\\Users\\ericb\\Desktop\\Research\\542_Project\\data\\test\\warranted_data_test_output\\mailparser_test_output_body' + str(i) + '.txt', 'w') as f:
        f.write(df_to_clean['body'][i])

# save df_to_clean['text_not_managed'][i] to txt file
for i in range(0, len(df_to_clean['text_not_managed'])):
    with open('C:\\Users\\ericb\\Desktop\\Research\\542_Project\\data\\test\\warranted_data_test_output\\mailparser_test_output_text_not_managed' + str(i) + '.txt', 'w') as f:
        f.write(df_to_clean['text_not_managed'][i])


نقدم لكم الخطة التدريبية لعام 2023 عبر الرابط التالي LINK_URL --- mail_boundary --- Content-Type: image/jpeg; name="image001.jpg" Content-Transfer-Encoding: base64 Content-ID: --- mail_boundary --- نقدم لكم الخطة التدريبية لعام 2023 عبر الرابط التالي LINK URL


# Adding Labels

- 0 for warranted
- 1 for unwarranted

In [66]:
# add labels to warranted and unwarranted data

input_directories = ['C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_no_duplicates_v2.csv', 
                     'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_no_duplicates_v2.csv']

output_csvs = ['C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_no_duplicates_with_labels_v2.csv',
                'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv']

for i in range(0, len(input_directories)):
    df = pd.read_csv(input_directories[i])
    df['label'] = i
    df.to_csv(output_csvs[i], index=False)

# Adding a few more features

- Number of unsafe links (http) ("UNSAFE_LINK_URL", "UNSAFE_IMAGE_URL", "UNSAFE_BUTTON_URL")
- Number of safe links (https) ("LINK_URL", "IMAGE_URL", " BUTTON_URL")
- Ratio of unsafe links to total links

In [67]:
import pandas as pd

# Path to your CSV file
# csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\warranted_cleaned_data_no_duplicates_with_labels_v2.csv'
# output_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\modified_warranted_cleaned_data_no_duplicates_with_labels_v2.csv'
csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv'
output_csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\modified_unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv'



# Load the CSV file into a DataFrame
df = pd.read_csv(csv_path)

# Define the URL types to count
url_types = ["UNSAFE_LINK_URL", "UNSAFE_IMAGE_URL", "UNSAFE_BUTTON_URL", 
             "LINK_URL", "IMAGE_URL", "BUTTON_URL"]

# Initialize columns for each URL type and for the percentage of unsafe links
for url_type in url_types:
    df[url_type + '_count'] = 0

df['unsafe_to_safe_link_ratio'] = 0.0

# Function to count occurrences of a substring in a string
def count_occurrences(text, substring):
    return text.count(substring) if pd.notna(text) else 0

# Iterate through each row to count occurrences and calculate percentages
for index, row in df.iterrows():
    total_unsafe_links = 0

    for url_type in url_types:
        count_body = count_occurrences(row['body'], url_type)
        count_subject = count_occurrences(row['subject'], url_type)
        total_count = count_body + count_subject

        # Update the count in the DataFrame
        df.at[index, url_type + '_count'] = total_count

        # Update total unsafe links count
        if "UNSAFE" in url_type:
            total_unsafe_links += total_count

    # Calculate the percentage of unsafe links
    total_links = row['total links in email']
    if total_links > 0:
        ratio = (total_unsafe_links / total_links)
        df.at[index, 'unsafe_to_safe_link_ratio'] = ratio

# Save the modified DataFrame back to CSV
df.to_csv(output_csv_path, index=False)

print(f"Modified CSV saved to {output_csv_path}")


Modified CSV saved to C:\Users\ericb\Desktop\Research\542_Project\cleaned_data\unwarranted_data\modified_unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv


In [68]:
df.head(50)

filename  \
0   1514898318.13268_223.txt   
1   1514898318.13268_225.txt   
2   1514898318.13268_229.txt   
3      1514911925.5197_1.txt   
4      1514911941.5199_1.txt   
5    1514911941.5199_101.txt   
6    1514911941.5199_103.txt   
7    1514911941.5199_105.txt   
8    1514911941.5199_107.txt   
9    1514911941.5199_109.txt   
10    1514911941.5199_11.txt   
11   1514911941.5199_111.txt   
12   1514911941.5199_113.txt   
13   1514911941.5199_115.txt   
14   1514911941.5199_117.txt   
15   1514911941.5199_119.txt   
16   1514911941.5199_121.txt   
17   1514911941.5199_123.txt   
18   1514911941.5199_125.txt   
19   1514911941.5199_127.txt   
20   1514911941.5199_129.txt   
21    1514911941.5199_13.txt   
22   1514911941.5199_131.txt   
23   1514911941.5199_133.txt   
24   1514911941.5199_135.txt   
25   1514911941.5199_137.txt   
26   1514911941.5199_139.txt   
27   1514911941.5199_141.txt   
28   1514911941.5199_143.txt   
29   1514911941.5199_145.txt   
30   1514911941.5199_147.txt   
31   1514911941.5199_149.txt   
32    1514911941.5199_15.txt   
33   1514911941.5199_151.txt   
34   1514911941.5199_153.txt   
35   1514911941.5199_155.txt   
36   1514911941.5199_157.txt   
37   1514911941.5199_159.txt   
38   1514911941.5199_161.txt   
39   1514911941.5199_163.txt   
40   1514911941.5199_165.txt   
41   1514911941.5199_167.txt   
42   1514911941.5199_169.txt   
43    1514911941.5199_17.txt   
44   1514911941.5199_171.txt   
45   1514911941.5199_173.txt   
46   1514911941.5199_175.txt   
47   1514911941.5199_177.txt   
48   1514911941.5199_179.txt   
49   1514911941.5199_181.txt   

                                                 body  \
0                                       Can we talk ?   
1   Science of Numerological Analysis UNSAFE_LINK_...   
2   These chicks are looking for casual sex and di...   
3   附件为18年计划表 --- mail_boundary --- Content-Type: ...   
4   Voted Top Gift for 2017! Stealth SmartCam! FRE...   
5                     UNSAFE_LINK_URL 】｀●┠◎´□⌒´∴㎡┳′〔★   
6   UNSAFE_LINK_URL male_sign〔√┘´＾⊂┓｝male_sign∫⊆┸┠...   
7                 UNSAFE_LINK_URL ゝ｛〃→⌒[Å∪≒〒×┣∇Å℃┛＼〓∈   
8                           UNSAFE_LINK_URL 「≦∬∥％┴▲☆′   
9                  UNSAFE_LINK_URL ┝］『＝│┌＞¨∵√♯￡┴◆∈→∵×   
10  Application facts - no out of pocket costs UNS...   
11                         UNSAFE_LINK_URL %┏…↑∽┬∈∥┓†   
12                              UNSAFE_LINK_URL ⊥≦∟＿⊃   
13                           UNSAFE_LINK_URL ┗［√∠⊂〇〔┿   
14  UNSAFE_LINK_URL ⊃┬∋▲≒〇┨√∝female_sign》［ゝmale_si...   
15                 UNSAFE_LINK_URL ≠■｛}〕┫┰∠┏┣⇒⌒∀｜…￢↑｝   
16  bruce:您好！ 《销售精英2天强化训练2018版》 本课程可根据企业需求制定内训，欢迎来...   
17                       UNSAFE_LINK_URL ┫）」)∽）」)⊂┝∃［   
18                UNSAFE_LINK_URL ＝┬°⊥≠└┸Å￣%〓│＾〕。◎≧(⌒   
19                            UNSAFE_LINK_URL ～┐》▽→┫㎡   
20                              UNSAFE_LINK_URL Å∠○┻＜   
21  Relieve Anxiety Today! Try CBD! UNSAFE_LINK_UR...   
22                      UNSAFE_LINK_URL ⇔｝☆※≠┠√┸┘′≒⊂｡   
23                UNSAFE_LINK_URL ∵〓}≠●÷〕〆‐╋｜￡．‐┌┓）」)   
24  bruce@bruce-guenter.dyndns.org PC MALLをご利用中のお客...   
25                           UNSAFE_LINK_URL 92640459   
26  The only thing you will need is:EMAIL This pro...   
27                         UNSAFE_LINK_URL ◇‥￥∋】┰┐]＾╂   
28     UNSAFE_LINK_URL │（∨♭♯｡∋○┰female_sign㎡★×｛├■〇▽≠∞   
29                        UNSAFE_LINK_URL ～￥∈※‰┸‐┃∋│⊿   
30                           UNSAFE_LINK_URL ∞…□∩■▲(㎡   
31  ���\\ufffdO�ɘA��������������񂾂��ǑS�R�A�����ĂȂ��...   
32  Are your meds part of America's deadly new hea...   
33                      UNSAFE_LINK_URL ～゜√＋〈〉´∽≦●∝゛㎡   
34                   UNSAFE_LINK_URL ∪｣≧┃∬〕´…Å〉┰┗□№⊥┌   
35                       UNSAFE_LINK_URL ％∠<┝∟│℃┘´┏∴〇   
36  bruce@bruce-guenter.dyndns.org パソコンメールをご利用中のお客...   
37                           UNSAFE_LINK_URL △］｝┤┛☆∈｢   
38                           UNSAFE_LINK_URL 92389340   
39                           UNSAFE_LINK_URL 92309724   
40                 UNSAFE_LINK_URL ─∟∀＋±｀】♯…］｝°‡』∝

In [73]:
# Path to your CSV file
# csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\warranted_data\\modified_warranted_cleaned_data_no_duplicates_with_labels_v2.csv'
csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\modified_unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv'



# Load the CSV file into a DataFrame
df = pd.read_csv(csv_path)

# count number of NaN values in each comments column
df['comments'].isna().sum()

# fill NaN values with empty string
df['comments'] = df['comments'].fillna('')

# save df
df.to_csv('C:\\Users\\ericb\\Desktop\\Research\\542_Project\\cleaned_data\\unwarranted_data\\modified_unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv', index=False)

In [63]:
df.head()

filename  \
0  1514898318.13268_223.txt   
1  1514898318.13268_225.txt   
2  1514898318.13268_229.txt   
3     1514911925.5197_1.txt   
4     1514911941.5199_1.txt   

                                                body  \
0                                      Can we talk ?   
1  Science of Numerological Analysis UNSAFE_LINK_...   
2  These chicks are looking for casual sex and di...   
3  附件为18年计划表 --- mail_boundary --- Content-Type: ...   
4  Voted Top Gift for 2017! Stealth SmartCam! FRE...   

                                             subject comments  \
0                                                 HI      NaN   
1                  Science of Numerological Analysis      NaN   
2         These chicks are looking for a booty call.      NaN   
3                                        回复：2018年计划表      NaN   
4  Voted Top Gift for 2017! Stealth SmartCam! FRE...      NaN   

                                          text_plain  \
0                                                 []   
1  ['Science of Numerological Analysis\n\n\nhttp:...   
2  ['\n\nThese chicks are looking for casual sex ...   
3  ['附件为18年计划表 ', 'Content-Type: application/octe...   
4  ['Voted Top Gift for 2017!  Stealth SmartCam! ...   

                                           text_html text_not_managed defects  \
0  ['<html><body><span style="font-family:Verdana...               []      []   
1  ['<html>\n<head>\n\t<title></title>\n</head>\n...               []      []   
2  ['<html>\n<head>\n\t<title></title>\n</head>\n...               []      []   
3  ['<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.0 ...               []      []   
4  ['<html>\n <head> \n  <title></title> \n  <met...               []      []   

  defects_categories  number of unsubscribe links  ...  email size (bytes)  \
0              set()                            0  ...                 318   
1              set()                            1  ...                6929   
2              set()                            0  ...                6812   
3              set()                            0  ...                 511   
4              set()                            0  ...                3131   

   dkim-signature  label  UNSAFE_LINK_URL_count UNSAFE_IMAGE_URL_count  \
0          Absent      1                      0                      0   
1         Present      1                      4                      0   
2          Absent      1                      2                      0   
3          Absent      1                      0                      0   
4         Present      1                      2                      0   

   UNSAFE_BUTTON_URL_count  LINK_URL_count  IMAGE_URL_count  BUTTON_URL_count  \
0                        0               0                0                 0   
1                        0               4                0                 0   
2                        0               2                0                 0   
3                        0               0                0                 0   
4                        0               2                0                 0   

   unsafe_to_safe_link_ratio  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0  

[5 rows x 23 columns]

In [64]:
csv_path = 'C:\\Users\\ericb\\Desktop\\Research\\542_Project\\train_test_data\\unwarranted_pre_shuffle\\modified_unwarranted_cleaned_data_no_duplicates_with_labels_v2.csv'

# Load the CSV file into a DataFrame
df = pd.read_csv(csv_path)

df.head()

filename  \
0  1514898318.13268_223.txt   
1  1514898318.13268_225.txt   
2  1514898318.13268_229.txt   
3     1514911925.5197_1.txt   
4     1514911941.5199_1.txt   

                                                body  \
0                                      Can we talk ?   
1  Science of Numerological Analysis UNSAFE_LINK_...   
2  These chicks are looking for casual sex and di...   
3  附件为18年计划表 --- mail_boundary --- Content-Type: ...   
4  Voted Top Gift for 2017! Stealth SmartCam! FRE...   

                                             subject comments  \
0                                                 HI      NaN   
1                  Science of Numerological Analysis      NaN   
2         These chicks are looking for a booty call.      NaN   
3                                        回复：2018年计划表      NaN   
4  Voted Top Gift for 2017! Stealth SmartCam! FRE...      NaN   

                                          text_plain  \
0                                                 []   
1  ['Science of Numerological Analysis\n\n\nhttp:...   
2  ['\n\nThese chicks are looking for casual sex ...   
3  ['附件为18年计划表 ', 'Content-Type: application/octe...   
4  ['Voted Top Gift for 2017!  Stealth SmartCam! ...   

                                           text_html text_not_managed defects  \
0  ['<html><body><span style="font-family:Verdana...               []      []   
1  ['<html>\n<head>\n\t<title></title>\n</head>\n...               []      []   
2  ['<html>\n<head>\n\t<title></title>\n</head>\n...               []      []   
3  ['<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.0 ...               []      []   
4  ['<html>\n <head> \n  <title></title> \n  <met...               []      []   

  defects_categories  number of unsubscribe links  ...  email size (bytes)  \
0              set()                            0  ...                 318   
1              set()                            1  ...                6929   
2              set()                            0  ...                6812   
3              set()                            0  ...                 511   
4              set()                            0  ...                3131   

   dkim-signature  label  UNSAFE_LINK_URL_count UNSAFE_IMAGE_URL_count  \
0          Absent      1                      0                      0   
1         Present      1                      4                      0   
2          Absent      1                      2                      0   
3          Absent      1                      0                      0   
4         Present      1                      2                      0   

   UNSAFE_BUTTON_URL_count  LINK_URL_count  IMAGE_URL_count  BUTTON_URL_count  \
0                        0               0                0                 0   
1                        0               4                0                 0   
2                        0               2                0                 0   
3                        0               0                0                 0   
4                        0               2                0                 0   

   unsafe_to_safe_link_ratio  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0  

[5 rows x 23 columns]